In [27]:
import numpy as np
from tensorflow.keras.datasets import imdb
import tensorflow as tf

# Load the integer sequence the IMDB dataset with Keras.
index_offset = 3  # word index offset
(x_train, y_train), (x_test, y_test) = imdb.load_data(num_words=1000,
                                                      index_from=index_offset)

print(y_train)
y_train = y_train.reshape(-1, 1)
y_test = y_test.reshape(-1, 1)
# Prepare the dictionary of index to word.
word_to_id = imdb.get_word_index()
word_to_id = {k: (v + index_offset) for k, v in word_to_id.items()}
# print(word_to_id)
# word_to_id["<PAD>"] = 0
# word_to_id["<START>"] = 1
# word_to_id["<UNK>"] = 2
id_to_word = {value: key for key, value in word_to_id.items()}
# print(id_to_word)
# Convert the word indices to words.
x_train = list(map(lambda sentence: ' '.join(
    id_to_word[i] for i in sentence), x_train))
x_test = list(map(lambda sentence: ' '.join(
    id_to_word[i] for i in sentence), x_test))
x_train = np.array(x_train, dtype=np.str)
x_test = np.array(x_test, dtype=np.str)
print(x_train.shape)  # (25000,)
print(y_train.shape)  # (25000, 1)
print(x_train[0][:50])  # <START> this film was just brilliant casting <UNK>

[1 0 0 ... 0 1 0]


KeyError: 1

In [2]:
import time
import math
import numpy as np
import matplotlib.pyplot as plt
from scipy.stats import pearsonr
import random
import pandas as pd
import os
Drugdata = []
druganwser = []
EPAdata = []
epaanwser = []
with open("../logP_labels.smi", "r") as EPA:
    with open("../alogptest.csv", "r") as DRUG:
        dlines = DRUG.readlines()
        Elines = EPA.readlines()
        for dline in dlines:
            dsl = dline.split()
            Drugdata.append(" ".join(dsl[0]))
            druganwser.append(dsl[1])
        for Eline in Elines:
            Esl = Eline.split()
            EPAdata.append(" ".join(Esl[0]))
            epaanwser.append(Esl[1])


x_train = np.array(EPAdata, dtype=np.str)
y_train = np.array(epaanwser, dtype=np.str)
x_test = np.array(Drugdata, dtype=np.str)
y_test = np.array(druganwser, dtype=np.str)
y_train = y_train.reshape(-1, 1)
y_test = y_test.reshape(-1, 1)
MAX_LENGTH = 400
SOS_token = 1
EOS_token = 2
PAD_token = 0


class Lang:
    def __init__(self, name):
        self.name = name
        self.word2index = {}
        self.word2count = {}
        self.index2word = {0: "PAD", 1: "SOS", 2: "EOS"}
        self.n_words = 3  # PAD 포함
        
    def addSentence(self, sentence):
        for word in sentence.split(' '):
            self.addWord(word)

    def addWord(self, word):
        if word not in self.word2index:
            self.word2index[word] = self.n_words
            self.word2count[word] = 1
            self.index2word[self.n_words] = word

            self.n_words += 1
        else:
            self.word2count[word] += 1


EPAlang = Lang("EPA")
Druglang = Lang("Drug")
E = []
D = []


def indexesFromSentence(lang, sentence):
    return [lang.word2index[word] for word in sentence.split(' ')]


def tensorFromSentence_encond(lang, sentence):
    indexes = indexesFromSentence(lang, sentence)
    while len(indexes) >= MAX_LENGTH:
        del indexes[MAX_LENGTH - 1]
    while len(indexes) < MAX_LENGTH:
        indexes.append(PAD_token)
    return indexes


def tensorsFromPair(EP):
    input_tensor = tensorFromSentence_encond(EPAlang, EP)
    return input_tensor


for EP in x_train:
    EPAlang.addSentence(EP)
    Druglang.addSentence(EP)
    ab = tensorsFromPair(EP)
    a = [str(ab[i]) for i in range(len(ab))]
    E.append(",".join(a))
for Dru in x_test:
    EPAlang.addSentence(Dru)
    Druglang.addSentence(Dru)
    ab = tensorsFromPair(Dru)
    a = [str(ab[i]) for i in range(len(ab))]
    D.append(",".join(a))
    


In [3]:
import autokeras as ak

# Initialize the text classifier.
clf = ak.TextRegressor(max_trials=100) # It tries 10 different models.
# Feed the text classifier with training data.
clf.fit(x_train, y_train, batch_size=1024)
# Predict with the best model.
predicted_y = clf.predict(x_test)
# Evaluate the best model with testing data.
print(clf.evaluate(x_test, y_test))

Train for 12 steps, validate for 3 steps
Epoch 1/1000
12/12 [==============================] - ETA: 6s - loss: 7.0908 - mean_squared_error: 7.09 - ETA: 3s - loss: 7.4436 - mean_squared_error: 7.44 - ETA: 2s - loss: 7.0519 - mean_squared_error: 7.05 - ETA: 1s - loss: 7.2120 - mean_squared_error: 7.21 - ETA: 1s - loss: 7.1411 - mean_squared_error: 7.14 - ETA: 1s - loss: 6.9988 - mean_squared_error: 6.99 - ETA: 0s - loss: 7.2348 - mean_squared_error: 7.23 - ETA: 0s - loss: 7.4734 - mean_squared_error: 7.47 - ETA: 0s - loss: 7.5225 - mean_squared_error: 7.52 - ETA: 0s - loss: 7.4526 - mean_squared_error: 7.45 - ETA: 0s - loss: 7.5381 - mean_squared_error: 7.53 - 2s 164ms/step - loss: 7.3301 - mean_squared_error: 7.5199 - val_loss: 7.4406 - val_mean_squared_error: 7.4486
Epoch 2/1000
12/12 [==============================] - ETA: 1s - loss: 6.8979 - mean_squared_error: 6.89 - ETA: 1s - loss: 7.2328 - mean_squared_error: 7.23 - ETA: 0s - loss: 6.8386 - mean_squared_error: 6.83 - ETA: 0s - los

12/12 [==============================] - ETA: 1s - loss: 3.6569 - mean_squared_error: 3.65 - ETA: 1s - loss: 3.5015 - mean_squared_error: 3.50 - ETA: 1s - loss: 3.2007 - mean_squared_error: 3.20 - ETA: 0s - loss: 3.0816 - mean_squared_error: 3.08 - ETA: 0s - loss: 3.0994 - mean_squared_error: 3.09 - ETA: 0s - loss: 3.0098 - mean_squared_error: 3.00 - ETA: 0s - loss: 3.0975 - mean_squared_error: 3.09 - ETA: 0s - loss: 3.1460 - mean_squared_error: 3.14 - ETA: 0s - loss: 3.1427 - mean_squared_error: 3.14 - ETA: 0s - loss: 3.1048 - mean_squared_error: 3.10 - ETA: 0s - loss: 3.0932 - mean_squared_error: 3.09 - 2s 125ms/step - loss: 2.9568 - mean_squared_error: 3.0813 - val_loss: 2.8542 - val_mean_squared_error: 2.8972
Epoch 13/1000
12/12 [==============================] - ETA: 1s - loss: 3.5021 - mean_squared_error: 3.50 - ETA: 1s - loss: 3.3368 - mean_squared_error: 3.33 - ETA: 1s - loss: 3.0585 - mean_squared_error: 3.05 - ETA: 0s - loss: 2.9426 - mean_squared_error: 2.94 - ETA: 0s - loss

12/12 [==============================] - ETA: 1s - loss: 2.3379 - mean_squared_error: 2.33 - ETA: 1s - loss: 2.3464 - mean_squared_error: 2.34 - ETA: 1s - loss: 2.2758 - mean_squared_error: 2.27 - ETA: 0s - loss: 2.1935 - mean_squared_error: 2.19 - ETA: 0s - loss: 2.1740 - mean_squared_error: 2.17 - ETA: 0s - loss: 2.0838 - mean_squared_error: 2.08 - ETA: 0s - loss: 2.0332 - mean_squared_error: 2.03 - ETA: 0s - loss: 1.9890 - mean_squared_error: 1.98 - ETA: 0s - loss: 1.9534 - mean_squared_error: 1.95 - ETA: 0s - loss: 1.9524 - mean_squared_error: 1.95 - ETA: 0s - loss: 1.9597 - mean_squared_error: 1.95 - 2s 135ms/step - loss: 1.8990 - mean_squared_error: 1.9543 - val_loss: 2.3185 - val_mean_squared_error: 2.3375
Epoch 24/1000
12/12 [==============================] - ETA: 1s - loss: 2.2801 - mean_squared_error: 2.28 - ETA: 1s - loss: 2.3009 - mean_squared_error: 2.30 - ETA: 1s - loss: 2.2346 - mean_squared_error: 2.23 - ETA: 0s - loss: 2.1542 - mean_squared_error: 2.15 - ETA: 0s - loss

12/12 [==============================] - ETA: 2s - loss: 2.0045 - mean_squared_error: 2.00 - ETA: 1s - loss: 2.0140 - mean_squared_error: 2.01 - ETA: 1s - loss: 1.9722 - mean_squared_error: 1.97 - ETA: 1s - loss: 1.9171 - mean_squared_error: 1.91 - ETA: 1s - loss: 1.9108 - mean_squared_error: 1.91 - ETA: 1s - loss: 1.8435 - mean_squared_error: 1.84 - ETA: 0s - loss: 1.7952 - mean_squared_error: 1.79 - ETA: 0s - loss: 1.7599 - mean_squared_error: 1.75 - ETA: 0s - loss: 1.7302 - mean_squared_error: 1.73 - ETA: 0s - loss: 1.7281 - mean_squared_error: 1.72 - ETA: 0s - loss: 1.7313 - mean_squared_error: 1.73 - 2s 197ms/step - loss: 1.6873 - mean_squared_error: 1.7275 - val_loss: 2.1318 - val_mean_squared_error: 2.1531
Epoch 35/1000
12/12 [==============================] - ETA: 2s - loss: 1.9714 - mean_squared_error: 1.97 - ETA: 1s - loss: 1.9737 - mean_squared_error: 1.97 - ETA: 1s - loss: 1.9364 - mean_squared_error: 1.93 - ETA: 1s - loss: 1.8863 - mean_squared_error: 1.88 - ETA: 1s - loss

12/12 [==============================] - ETA: 2s - loss: 1.7295 - mean_squared_error: 1.72 - ETA: 2s - loss: 1.6378 - mean_squared_error: 1.63 - ETA: 1s - loss: 1.6273 - mean_squared_error: 1.62 - ETA: 1s - loss: 1.6121 - mean_squared_error: 1.61 - ETA: 1s - loss: 1.6268 - mean_squared_error: 1.62 - ETA: 1s - loss: 1.5851 - mean_squared_error: 1.58 - ETA: 1s - loss: 1.5657 - mean_squared_error: 1.56 - ETA: 0s - loss: 1.5517 - mean_squared_error: 1.55 - ETA: 0s - loss: 1.5388 - mean_squared_error: 1.53 - ETA: 0s - loss: 1.5378 - mean_squared_error: 1.53 - ETA: 0s - loss: 1.5374 - mean_squared_error: 1.53 - 2s 203ms/step - loss: 1.4988 - mean_squared_error: 1.5340 - val_loss: 1.9074 - val_mean_squared_error: 1.9282
Epoch 46/1000
12/12 [==============================] - ETA: 1s - loss: 1.7201 - mean_squared_error: 1.72 - ETA: 1s - loss: 1.6290 - mean_squared_error: 1.62 - ETA: 1s - loss: 1.6174 - mean_squared_error: 1.61 - ETA: 1s - loss: 1.6015 - mean_squared_error: 1.60 - ETA: 1s - loss

...

Train for 12 steps, validate for 3 steps
Epoch 1/1000
12/12 [==============================] - ETA: 14s - loss: 7.0908 - mean_squared_error: 7.090 - ETA: 8s - loss: 7.4237 - mean_squared_error: 7.423 - ETA: 6s - loss: 7.0127 - mean_squared_error: 7.01 - ETA: 4s - loss: 7.1462 - mean_squared_error: 7.14 - ETA: 4s - loss: 7.0522 - mean_squared_error: 7.05 - ETA: 3s - loss: 6.8851 - mean_squared_error: 6.88 - ETA: 2s - loss: 7.0865 - mean_squared_error: 7.08 - ETA: 2s - loss: 7.2813 - mean_squared_error: 7.28 - ETA: 1s - loss: 7.2927 - mean_squared_error: 7.29 - ETA: 0s - loss: 7.1879 - mean_squared_error: 7.18 - ETA: 0s - loss: 7.2213 - mean_squared_error: 7.22 - 6s 503ms/step - loss: 6.9774 - mean_squared_error: 7.1999 - val_loss: 7.0492 - val_mean_squared_error: 7.0588
Epoch 2/1000
12/12 [==============================] - ETA: 4s - loss: 6.0589 - mean_squared_error: 6.05 - ETA: 3s - loss: 6.2636 - mean_squared_error: 6.26 - ETA: 3s - loss: 5.8125 - mean_squared_error: 5.81 - ETA: 3s - 

12/12 [==============================] - ETA: 3s - loss: 3.0698 - mean_squared_error: 3.06 - ETA: 3s - loss: 2.9018 - mean_squared_error: 2.90 - ETA: 3s - loss: 2.7280 - mean_squared_error: 2.72 - ETA: 2s - loss: 2.6404 - mean_squared_error: 2.64 - ETA: 2s - loss: 2.6410 - mean_squared_error: 2.64 - ETA: 2s - loss: 2.5474 - mean_squared_error: 2.54 - ETA: 1s - loss: 2.5642 - mean_squared_error: 2.56 - ETA: 1s - loss: 2.5326 - mean_squared_error: 2.53 - ETA: 1s - loss: 2.4864 - mean_squared_error: 2.48 - ETA: 0s - loss: 2.4588 - mean_squared_error: 2.45 - ETA: 0s - loss: 2.4596 - mean_squared_error: 2.45 - 4s 365ms/step - loss: 2.3937 - mean_squared_error: 2.4539 - val_loss: 5.3280 - val_mean_squared_error: 5.3465
Epoch 13/1000
12/12 [==============================] - ETA: 3s - loss: 2.7093 - mean_squared_error: 2.70 - ETA: 3s - loss: 2.5519 - mean_squared_error: 2.55 - ETA: 3s - loss: 2.4499 - mean_squared_error: 2.44 - ETA: 2s - loss: 2.3919 - mean_squared_error: 2.39 - ETA: 2s - loss

INFO:tensorflow:Oracle triggered exit
Train for 15 steps, validate for 3 steps
Epoch 1/1000
15/15 [==============================] - ETA: 22s - loss: 7.0941 - mean_squared_error: 7.094 - ETA: 17s - loss: 7.4233 - mean_squared_error: 7.423 - ETA: 14s - loss: 7.0135 - mean_squared_error: 7.013 - ETA: 13s - loss: 7.1508 - mean_squared_error: 7.150 - ETA: 11s - loss: 7.0620 - mean_squared_error: 7.062 - ETA: 10s - loss: 6.9009 - mean_squared_error: 6.900 - ETA: 9s - loss: 7.1128 - mean_squared_error: 7.112 - ETA: 7s - loss: 7.3241 - mean_squared_error: 7.32 - ETA: 6s - loss: 7.3502 - mean_squared_error: 7.35 - ETA: 5s - loss: 7.2601 - mean_squared_error: 7.26 - ETA: 4s - loss: 7.3187 - mean_squared_error: 7.31 - ETA: 3s - loss: 7.0752 - mean_squared_error: 7.29 - ETA: 2s - loss: 6.9721 - mean_squared_error: 7.16 - ETA: 1s - loss: 7.0504 - mean_squared_error: 7.23 - 16s 1s/step - loss: 7.0314 - mean_squared_error: 7.2024 - val_loss: 6.5566 - val_mean_squared_error: 6.5684
Epoch 2/1000
15/15

Epoch 10/1000
15/15 [==============================] - ETA: 13s - loss: 3.4405 - mean_squared_error: 3.440 - ETA: 12s - loss: 3.2405 - mean_squared_error: 3.240 - ETA: 11s - loss: 2.9874 - mean_squared_error: 2.987 - ETA: 10s - loss: 2.9110 - mean_squared_error: 2.911 - ETA: 9s - loss: 2.9648 - mean_squared_error: 2.964 - ETA: 8s - loss: 2.9026 - mean_squared_error: 2.90 - ETA: 7s - loss: 3.0376 - mean_squared_error: 3.03 - ETA: 6s - loss: 3.1294 - mean_squared_error: 3.12 - ETA: 5s - loss: 3.1644 - mean_squared_error: 3.16 - ETA: 5s - loss: 3.1529 - mean_squared_error: 3.15 - ETA: 4s - loss: 3.1762 - mean_squared_error: 3.17 - ETA: 2s - loss: 3.0258 - mean_squared_error: 3.16 - ETA: 1s - loss: 2.9938 - mean_squared_error: 3.11 - ETA: 0s - loss: 3.0690 - mean_squared_error: 3.18 - 15s 1s/step - loss: 3.0448 - mean_squared_error: 3.1560 - val_loss: 3.1218 - val_mean_squared_error: 3.1640
Epoch 11/1000
15/15 [==============================] - ETA: 14s - loss: 3.4517 - mean_squared_error:

44/44 [==============================] - ETA: 6s - loss: 21.4009 - mean_squared_error: 21.40 - ETA: 3s - loss: 14.0964 - mean_squared_error: 14.09 - ETA: 1s - loss: 8.3241 - mean_squared_error: 8.3241 - ETA: 0s - loss: 6.9504 - mean_squared_error: 6.95 - ETA: 0s - loss: 6.7274 - mean_squared_error: 6.72 - ETA: 0s - loss: 6.6785 - mean_squared_error: 6.67 - ETA: 0s - loss: 6.5547 - mean_squared_error: 6.55 - ETA: 0s - loss: 6.6754 - mean_squared_error: 6.67 - ETA: 0s - loss: 6.2966 - mean_squared_error: 6.29 - ETA: 0s - loss: 6.1234 - mean_squared_error: 6.12 - 1s 16ms/step - loss: 6.3321 - mean_squared_error: 6.2618
[6.332131843675267, 6.2617526]


In [ ]:
print(clf.export_model())


In [6]:

print(clf.evaluate(x_test, y_test))

44/44 [==============================] - ETA: 10s - loss: 21.4009 - mean_squared_error: 21.400 - ETA: 1s - loss: 8.8468 - mean_squared_error: 8.8468  - ETA: 0s - loss: 6.9504 - mean_squared_error: 6.95 - ETA: 0s - loss: 6.6039 - mean_squared_error: 6.60 - ETA: 0s - loss: 6.6970 - mean_squared_error: 6.69 - ETA: 0s - loss: 6.2569 - mean_squared_error: 6.25 - 1s 13ms/step - loss: 6.3321 - mean_squared_error: 6.2618
[6.332131843675267, 6.2617526]


In [4]:

predicted_y = clf.predict(x_test)

In [5]:
predicted_y

array([[1.9617391],
       [1.9617391],
       [1.9617391],
       ...,
       [1.9617391],
       [1.9617391],
       [1.9617391]], dtype=float32)

In [41]:

clf = ak.TextRegressor(max_trials=10) # It tries 10 different models.
# Feed the text classifier with training data.